In [ ]:
using Pkg
Pkg.add("SolidStateDetectors")
Pkg.add("Unitful")
Pkg.add("Plots")

In [ ]:
using SolidStateDetectors, Unitful, Plots

In [ ]:
# Configuration file which describes the geometry, impurity density, applied potentials, ...
# You might need to add the absolute path to where "BEGe.yaml" was saved
config_file = "BEGe.yaml"

In [ ]:
# open(f -> print.(readlines(f)[1:26] .* "\n"), config_file);
# open(f -> print.(readlines(f)[27:end] .* "\n"), config_file);

In [ ]:
sim = Simulation{Float64}(config_file)
plot(sim.detector, size = (500,500))

In [ ]:
calculate_electric_potential!(sim, refinement_limits = [0.2, 0.1, 0.05, 0.03, 0.02])
plot(sim.electric_potential, full_det = true)

In [ ]:
calculate_electric_field!(sim)
plot(sim.electric_field, full_det = true, clims = (0, 5e5))
plot_electric_fieldlines!(sim)

In [ ]:
for i in 1:2
    calculate_weighting_potential!(sim, i) 
end
plot(sim.weighting_potentials[1], full_det = true)

In [ ]:
cdm = ADLChargeDriftModel(T = Float64)
sim.detector = SolidStateDetector(sim.detector, cdm)

In [ ]:
locations = [CartesianPoint(0.035,0,0.02), CartesianPoint(-0.015,0,0.015)]
energies = [1000u"keV", 300u"keV"]
evt = Event(locations, energies)
evt.waveforms

In [ ]:
simulate!(evt, sim, Δt = 1u"ns")

In [ ]:
plot(sim.detector, size = (500,500))
plot!(evt.drift_paths, legendfontsize = 10)
plot!(vcat(evt.locations...), color = :orange, markersize = 6, label = "")

In [ ]:
plot(u"ns", u"fC")
plot!(add_baseline_and_extend_tail.(evt.waveforms, 0, 1000), linewidth = 2, legend = false)

  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />  <br />

# Simulating a radial scan into the bulk of the detector

In [ ]:
evts = Event{Float64}[]
for r in 0.01:0.002:0.036
    locations = [CartesianPoint(r, 0, 0.02)]
    energies = [1000u"keV"]
    evt0 = Event(locations, energies)
    simulate!(evt0, sim, Δt = 1u"ns")
    push!(evts, deepcopy(evt0))
end

In [ ]:
plot(broadcast(evt -> add_baseline_and_extend_tail(evt.waveforms[2],100,1000), evts), 
    label = "r = " .* string.(collect(10:2:36)') .* "mm", linewidth = 2, legend = :bottomright)

# Simulating a C-V curve

In [ ]:
using ProgressMeter
Urange = 500:100:3500
C = typeof(1.0u"pF")[]
@showprogress for U in Urange
    sim.detector = SolidStateDetector(sim.detector, contact_potential = U, contact_id = 1)
    calculate_electric_potential!(sim, depletion_handling = true, verbose = false, refinement_limits = [0.2,0.1,0.05])
    for i in 1:2
        calculate_weighting_potential!(sim, i, depletion_handling = true, verbose = false, refinement_limits = [0.2,0.1,0.05])
    end
    push!(C, calculate_mutual_capacitance(sim, (1,2)))
end

In [ ]:
scatter(Urange, -C, xlabel = "Voltage", ylabel = "Capacitance")